In [56]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn import preprocessing
from scipy.optimize import curve_fit
mobile = np.load('/home/is/shuntaro-o/dev/compare_population_and_tweet_number/data/mobile/Kyoto/Kyotostation.npy')
twitter = np.load('/home/is/shuntaro-o/dev/compare_population_and_tweet_number/data/twitter/Kyoto/Kyotostaion2022/Kyotostation_3zi_2022.npy')


In [57]:
#外れ値の処理
twitter[96,17] = 8

In [58]:
mobile_flatten = mobile.flatten()
twitter_flatten = twitter.flatten()

## 一時間ごと

In [59]:
mobile_flatten_stand =preprocessing.scale(mobile_flatten)
twitter_flatten_stand = preprocessing.scale(twitter_flatten)

In [60]:
day_list_long = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28','29','30','31']
day_list_short = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28','29','30']
day_list_Feb = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28']
hour_list = ['00','01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23']
x_label = []
for month in ['01','02','03','04','05','06','07','08','09','10','11','12']:
    if month in ['01', '03', '05', '07', '08','10', '12']:
        day_list = day_list_long
    elif month == '02':
        day_list = day_list_Feb
    else:
        day_list = day_list_short
    for day in day_list:
        for hour in range(0,24):
            hour = str(hour)
            key = int('21'+ month + day + hour)
            key = str(key)
            x_label.append(key)

In [61]:
import plotly.graph_objects as go
fig = go.Figure(data=[
    go.Scatter(x=x_label, y=mobile_flatten_stand, name='mobile'),
    go.Scatter(x=x_label, y=twitter_flatten_stand, name="twitter"),
])
fig.show()

In [62]:
# x: input(人口)
def exp(x, k=1):
    rvalue = 0.0
    rvalue =  np.exp(k*x)
    return rvalue
def line(x,a=2):
    return a*x
def power(x, k=(1/4)):
    return (x**k)

In [63]:
x = mobile_flatten
y= twitter_flatten
#x = x/(sum(x)/sum(y))
popt_exp, pcov_exp = curve_fit(exp, x, y, p0=[0.001])
popt_line, pcov_line = curve_fit(line, x, y)
popt_power, pcov_power = curve_fit(power, x, y, p0=[ 1])

In [64]:
print(f'{popt_exp} {popt_line} {popt_power}')

[9.45188932e-05] [0.00066958] [0.27351455]


In [65]:
np.exp(popt_exp)

array([1.00009452])

In [66]:
fitting_exp = exp(x, *popt_exp)
fitting_line = line(x, *popt_line)
fitting_power = power(x, *popt_power)

In [67]:
import plotly.graph_objects as go
fig = go.Figure(data=[
    #go.Scatter(x=x_label, y=mobile_flatten_stand, name='mobile'),
    go.Scatter(x=x_label, y=twitter_flatten, name="twitter"),
    go.Scatter(x=x_label, y=fitting_exp, name="exp"),
    go.Scatter(x=x_label, y=fitting_line, name="line"),
    go.Scatter(x=x_label, y=fitting_power, name="power"),
])
fig.show()

In [68]:
o =twitter_flatten #実測データ例
e = fitting_exp #モデル計算された数値例
residuals =  o - e #残渣
rss = np.sum(residuals**2)      #残差平方和: residual sum of squares = rss
tss = np.sum((o-np.mean(o))**2) #全平方和: total sum of squares = tss
r_squared = 1 - (rss / tss)     #決定係数R^2
 
print(f'exp決定係数: {r_squared}')
#カイ２乗誤差
print(f'expカイ２乗誤差: {np.sum(((o-e)**2)/e)}')
print(f'exp平均２乗誤差: {np.sum(((o-e)**2)/(len(e)))}')

exp決定係数: 0.02286090831751819
expカイ２乗誤差: 146509.44659543267
exp平均２乗誤差: 116.88730558045347


In [69]:
o =twitter_flatten #実測データ例
e = fitting_line #モデル計算された数値例
residuals =  o - e #残渣
rss = np.sum(residuals**2)      #残差平方和: residual sum of squares = rss
tss = np.sum((o-np.mean(o))**2) #全平方和: total sum of squares = tss
r_squared = 1 - (rss / tss)     #決定係数R^2
 
print(f'line決定係数: {r_squared}')
#カイ２乗誤差
print(f'lineカイ２乗誤差: {np.sum(((o-e)**2)/e)}')
print(f'line平均２乗誤差: {np.sum(((o-e)**2)/(len(e)))}')

line決定係数: 0.2860289546170539
lineカイ２乗誤差: 54209.9907691731
line平均２乗誤差: 85.40662477598468


In [70]:
o =twitter_flatten #実測データ例
e = fitting_power #モデル計算された数値例
residuals =  o - e #残渣
rss = np.sum(residuals**2)      #残差平方和: residual sum of squares = rss
tss = np.sum((o-np.mean(o))**2) #全平方和: total sum of squares = tss
r_squared = 1 - (rss / tss)     #決定係数R^2
 
print(f'power決定係数: {r_squared}')
#カイ２乗誤差
print(f'powerカイ２乗誤差: {np.sum(((o-e)**2)/e)}')
print(f'power平均２乗誤差: {np.sum(((o-e)**2)/(len(e)))}')

power決定係数: 0.1423908439125975
powerカイ２乗誤差: 59847.9849102762
power平均２乗誤差: 102.58889890852596


## 一日ごと

In [71]:
mobile_perday = np.sum(mobile, axis=1)
twitter_perday = np.sum(twitter, axis=1)

In [72]:
mobile_perday_stand =preprocessing.scale(mobile_perday)
twitter_perday_stand = preprocessing.scale(twitter_perday)

In [73]:
day_list_long = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28','29','30','31']
day_list_short = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28','29','30']
day_list_Feb = ['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28']
x_label_perday = []
for month in ['01','02','03','04','05','06','07','08','09','10','11','12']:
    if month in ['01', '03', '05', '07', '08','10', '12']:
        day_list = day_list_long
    elif month == '02':
        day_list = day_list_Feb
    else:
        day_list = day_list_short
    for day in day_list:
        key = int('21'+ month + day)
        key = str(key)
        x_label_perday.append(key)

In [74]:
import plotly.graph_objects as go
fig = go.Figure(data=[
    go.Scatter(x=x_label_perday, y=mobile_perday_stand, name='mobile'),
    go.Scatter(x=x_label_perday, y=twitter_perday_stand, name="twitter"),
])
fig.show()